In [ ]:
!pip3 install -U langgraph
!pip3 install -U langchain
!pip3 install grandalf

In [63]:
# ！/usr/bin env python3
# -*- coding: utf-8 -*-
# author: yangyunlong time:2024/2/28
from typing import TypedDict, Annotated, Union, Optional, Type, List, Annotated, Sequence
 
import requests
from langchain.pydantic_v1 import BaseModel, Field
from langchain.tools import BaseTool, tool
from langchain_core.agents import AgentAction
from langchain_core.agents import AgentFinish
from langchain_core.messages import BaseMessage, SystemMessage, HumanMessage, AIMessage
from langgraph.graph import END, StateGraph
from langgraph.prebuilt.tool_executor import ToolExecutor
from langchain.chat_models import QianfanChatEndpoint
import qianfan
from langgraph.graph.message import add_messages
from functools import partial
from qianfan.extensions.langchain.agents import QianfanSingleActionAgent
from langchain.agents import AgentExecutor

import os

# 请填入您的AK和SK
os.environ['QIANFAN_AK'] = 'Your_AK'
os.environ['QIANFAN_SK'] = 'Your_SK'

# 请填入使用的模型
qianfan_chat_model = QianfanChatEndpoint(model='ERNIE-3.5-8K')

# 客服智能体的Tool和System Prompt定义
system_customer_support_agent = '''你是小店平台的客服路由工具。尽量不直接回话，而是通过工具完成客户咨询。你的主要职责是根据客户咨询的问题，提供对应的服务。如果客户咨询修改地址，申请运费补偿等问题，请调用对应的工具将任务委托给合适的专业助手。你自己无法做出这些类型的改变只有专业助手被授权为用户执行这些操作。用户不知道不同的专业助理，因此不要提及他们，直接通过函数委派任务即可'''
@tool("ToOrderAddressUpdateAssistant")
def ToOrderAddressUpdateAssistant(content: str) -> str:
    """将工作转交给专门的助手处理更新订单收货地址的事件"""
    # do nothing
    print('调用了ToOrderAddressUpdateAssistant函数')
    return '触发后面的更新订单收货地址的助手'

@tool("ToOrderApplyShippingFeeAgent")
def ToOrderApplyShippingFeeAgent(content: str) -> str:
    """将工作转交给专门的助手处理申请运费补偿的事件"""
    # do nothing
    print('调用了ToOrderApplyShippingFeeAgent函数')
    return '触发后面的申请运费补偿的助手'

# 客服智能体的Agent和Executor定义
tools_customer_support_agent = [ToOrderAddressUpdateAssistant, ToOrderApplyShippingFeeAgent]
qianfan_customer_support_agent = QianfanSingleActionAgent.from_system_prompt(tools_customer_support_agent, qianfan_chat_model, system_prompt=SystemMessage(system_customer_support_agent))
excutor_customer_support_agent = AgentExecutor(agent=qianfan_customer_support_agent, tools=tools_customer_support_agent, verbose=True)

# 地址更新智能体的Tool和System Prompt定义
system_addr_update_agent = '''你是一个引导客户进行修改地址的助手，当客户需要修改地址信息的时候，主助手会将委托你进行工作。根据客户提供到的信息，按照以下步骤引导客户完成修改地址的操作。
1.如果客户没有提供订单信息，请先调用ask_for_order引导客户提供订单信息
2.如果客户提供的订单信息，请调用ask_for_address引导客户提供新的地址信息
3.如果客户提供了新的地址信息，请调用update_address更新地址

请记住，如果客户终止了意图，请调用intent_interrupt工具退出
以下是一些您应该intent_interrupt的示例：
- 算了，我不想改了
- 等等，我在想一下
- 转人工
- 再见
- 我不想修改地址了
请记住，如果客户改变了意图，请调用CompleteOrEscalate交给主助手，不要创建无效的工具或函数。
以下是一些您应该CompleteOrEscalate的示例：
- 帮我申请运费
- 帮我取消订单
'''
@tool("ask_for_order")
def ask_for_order(content: str) -> str:
    """向用户索要订单信息。"""
    print('调用ask_for_order')
    return '请提供订单信息'

@tool("ask_for_address")
def ask_for_address(content: str) -> str:
    """向用户索要新的地址信息。"""
    print('调用ask_for_address')
    return '请提供新的地址信息'

@tool("update_address")
def update_address(content: str) -> str:
    """更新新地址"""
    print('调用update_address')
    # 调用API更新地址
    return '已完成地址更新，感谢使用'

@tool("intent_interrupt")
def intent_interrupt(content: str) -> str:
    """用户取消，退出"""
    print('调用intent_interrupt')
    return '用户取消，退出'

@tool("CompleteOrEscalate")
def CompleteOrEscalate(content: str) -> str:
    """A tool to mark the current task as completed and/or to escalate control of the dialog to the main assistant,
    who can re-route the dialog based on the user's needs."""
    # do nothing
    print('调用CompleteOrEscalate')
    return '任务完成交给上游智能体'


tools_addr_update_agent = [ask_for_order, ask_for_address, update_address, intent_interrupt, CompleteOrEscalate]
qianfan_addr_update_agent = QianfanSingleActionAgent.from_system_prompt(tools_addr_update_agent, qianfan_chat_model, system_prompt=SystemMessage(system_addr_update_agent))
excutor_addr_update_agent = AgentExecutor(agent=qianfan_addr_update_agent, tools=tools_addr_update_agent, verbose=True)

class State(TypedDict):
    # messages have the type "list".
    # The add_messages function appends messages to the list, rather than overwriting them
    order_id: str
    address: str
    messages: Annotated[list, add_messages]

graph_builder = StateGraph(State)

def customer_support_agent_rec_act(state):
    # print(state['messages'])
    result_customer_support_agent = excutor_customer_support_agent.invoke(state['messages'])
    # return {'messages': [AIMessage(content=result_customer_support_agent['output'])]}
    return {'messages': []}

def addr_update_agent_rec_act(state):
    print(state['messages'])
    result_addr_update_agent = excutor_addr_update_agent.invoke(state['messages'])
    return {'messages': [AIMessage(content=result_addr_update_agent['output'])]}


graph_builder.add_node("客服智能体", customer_support_agent_rec_act)
graph_builder.add_node("更新地址的助手", addr_update_agent_rec_act)

graph_builder.add_edge("客服智能体", "更新地址的助手")

graph_builder.set_entry_point("客服智能体")

app = graph_builder.compile()

## 打印图结构
app.get_graph().print_ascii()

## 第一轮对话：用户输入，想要修改地址
input_1st = "我想修改地址"
result = app.invoke({
    "messages": [{"role": "user", "content": input_1st}]
})
## 拿到输出
output_1st = result['messages'][-1].content

print("########### 第一轮对话 ##########")
print("输入：" + input_1st)
print("输出：" + output_1st)

# output_1st = '好的，为了进行地址修改，我需要您提供一下订单信息。请您告诉我您的订单号或者其他相关的订单信息。'

## 第二轮对话：用户输入，订单号123456789
input_2nd = "我的订单是123456789"
result = app.invoke({
    "messages": [
        {"role": "user", "content": input_1st},
        {"role": "assistant", "content": output_1st},
        {"role": "user", "content": input_2nd}
    ]
})
## 拿到输出
output_2nd = result['messages'][-1].content

print("########### 第二轮对话 ##########")
print("输入：" + input_2nd)
print("输出：" + output_2nd)

## 第三轮对话：用户输入，地址是上海市杨浦区
input_3rd = "地址是上海市杨浦区"
result = app.invoke({
    "messages": [
        {"role": "user", "content": input_1st},
        {"role": "assistant", "content": output_1st},
        {"role": "user", "content": input_2nd},
        {"role": "assistant", "content": output_2nd},
        {"role": "user", "content": input_3rd},
    ]
})
## 拿到输出
output_3rd = result['messages'][-1].content

print("########### 第二轮对话 ##########")
print("输入：" + input_3rd)
print("输出：" + output_3rd)



+-----------+  
| __start__ |  
+-----------+  
      *        
      *        
      *        
  +-------+    
  | 客服智能体 |    
  +-------+    
      *        
      *        
      *        
 +---------+   
 | 更新地址的助手 |   
 +---------+   


> Entering new AgentExecutor chain...
content='' additional_kwargs={'id': 'as-u7gsm46d2j', 'object': 'chat.completion', 'created': 1721224027, 'result': '', 'is_truncated': False, 'need_clear_history': False, 'function_call': {'name': 'ToOrderAddressUpdateAssistant', 'arguments': '{"content":"我想修改地址"}'}, 'finish_reason': 'function_call', 'usage': {'prompt_tokens': 225, 'completion_tokens': 26, 'total_tokens': 251}} response_metadata={'token_usage': {'prompt_tokens': 225, 'completion_tokens': 26, 'total_tokens': 251}, 'model_name': 'ERNIE-Bot', 'finish_reason': 'function_call', 'id': 'as-u7gsm46d2j', 'object': 'chat.completion', 'created': 1721224027, 'result': '', 'is_truncated': False, 'need_clear_history': False, 'function_call': {'name': 'ToOrde